In [1]:
# Importing libraries
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from plotly import tools
# import plotly.plotly as py
import chart_studio.plotly
from plotly.offline import init_notebook_mode, iplot
init_notebook_mode(connected=True)
import plotly.graph_objs as go
import plotly.figure_factory as ff
from IPython.display import HTML, Image
import plotly.express as px
px.set_mapbox_access_token(open(".mapbox_token").read())
import datetime 

In [2]:
import pandas as pd
birds = pd.read_csv("bird_tracking.csv")

In [3]:
birds['year'] = pd.to_datetime(birds['date_time']).dt.year
birds['month']= pd.to_datetime(birds['date_time']).dt.month
birds['hour'] = pd.to_datetime(birds['date_time']).dt.hour
birds['log_altitude'] = np.log2(birds['altitude'].clip(lower=1))

In [4]:
birds['day or night'] = birds.apply(lambda d: 'night' if pd.to_datetime(d['date_time']).hour >= 18 or pd.to_datetime(d['date_time']).hour <=  5 else 'day', axis = 1)
birds_night = birds[birds['day or night']== 'night']
birds_day = birds[birds['day or night']== 'day']

# Overview 
- The data focuses on three birds named Nico Sanne and Eric, it tracks their migration from late 2013 to early 2014
- Headers explain the data we are looking at in particular 
- Questions we are asking are posed before the code and output
- After the output there are explainations/analysis of results 
- These explainations determine differences/characteristics of the three birds in terms of the presented data and form some conclusions

## The following is based on data from August

Do the birds differ in average altitude flown during the month of August?

In [5]:
august = birds[birds['month']==8]
august.set_index('date_time').groupby('bird_name')['log_altitude'].mean().to_frame().reset_index()

bird_name  log_altitude
0      Eric      6.562098
1      Nico      6.706361
2     Sanne      6.075402

It appears that during the month of August Nico flies the highest on average. This could mean that the terrain he is flying over is higher above sea level then that of Eric and Sanne. This is especially true when compared to Sanne who has the lowest altitude on average in August. This would mean that in all likelihood Sanne flies closer to sea level on average in August as her average altitude is significantly lower. 

Is there a difference in flight patterns and activity between the three birds in both the day and night time?<br>                                                                           NOTE: The gaps in the map are from it swtiched from day to night and vice versa if we looked at August as a whole there would be no gaps in flight paths

In [29]:
day_aug = birds_day[birds_day['month'] == 8]
px.set_mapbox_access_token(open(".mapbox_token").read())
fig = px.scatter_mapbox(day_aug, lat="latitude", lon="longitude", color = "bird_name",
                  color_continuous_scale=px.colors.cyclical.IceFire,size = 'log_altitude',size_max= 5, zoom=3)
fig.show()

In [27]:
night_aug = birds_night[birds_night['month'] == 8]
px.set_mapbox_access_token(open(".mapbox_token").read())
fig = px.scatter_mapbox(night_aug, lat="latitude", lon="longitude", color = "bird_name",
                  color_continuous_scale=px.colors.cyclical.IceFire,size = 'log_altitude',size_max= 5, zoom=3)
fig.show()

In August whether it is night or day time Sanne is significantly more active in her flight path than either Nico or Eric who actually seem to share a space in France near Belgium that they flew around consistently. Sanne appears to travel the coast frequently during this month both North and South while Nico and Eric tend to stay inland not moving much from their area they have established for themselves. Sanne is much more active and diverse in her flight path when compared to Nico and Eric during August during both specified times. In regards to our first question answered this confirms our conjecture that during August Sanne flies closer to sea level based on her altitude average as we can clearly see her path is often on the sea's coast or directly above the water itself. As expected as well from their altitude averages for the month overall in August Nico and Eric mostly stay inland.

## The following data is from November to February (when I suspect their migration paths differ the most)

In [8]:
migration_df = birds[(birds['month']==9) | (birds['month']== 10) | (birds['month']== 11) | (birds['month']== 12| (birds['month']== 1) | (birds['month']== 2))  ]

How is each of the three bird's migration path different and where do they each end up for the winter and even further can we determine their species off their migration path?

In [28]:
px.set_mapbox_access_token(open(".mapbox_token").read())
fig = px.scatter_mapbox(migration_df, lat="latitude", lon="longitude", color = "bird_name",
                  color_continuous_scale=px.colors.cyclical.IceFire,size = 'log_altitude',size_max= 5, zoom=3)
fig.show()

It appears from looking at the three birds migration path that Eric not only stays closer to the coast in his flight path as he migrates, but he also does not cover as much distance as Nico or Sanne. He begins in France around Nico but only ends up getting to around Morroco by the time February is over. This could potentially be a place with a climate that suits him to stay warm in the dead of winter. Unlike Eric, Nico and Sanne fly past the coast of Morroco during this period, but then go even further south past the Sahara Dessert ending up around Senegal and Mauritania. Sanne and Nico also decide at the beginning of their journey to fly above the ocean which is different from Eric who tries to stay closer to the coast line most of his trip. From external research based on these migration patterns I am able to make a solid guess as to what species of birds these are. According to rspb.org Swallows begin around France and end up around Moroco or Southern Africa which is the quailties of Eric, Nico, and Sanne therefore it is possible that they are all Swallows. Sanne does start around France like the rest but she started her migration much sooner than the other two hence her starting in Portugal in this map. Her start time is another key diffrence between Sanne and her fellow potential Swallows. 

Since Sanne ends up further than the rest of the birds is her distribution of speed faster than the others or is it slower since she began her path sooner?

In [10]:
fig = px.box(migration_df, x='bird_name', y='speed_2d', color='bird_name')
fig.show()

It turns out that Sanne is right in the middle of the pack when it comes to speed during these months of migration. This makes complete sense as being further on her journey she does not need to fly as fast, but still has a sense of urgency because her path is much longer than Erics who is the slowest as he ends in Morroco which is the closest of the three to their start point so there is not as much of a need to go fast for him. Similarily Nico is the fastest during this time which also makes sense as unlike Sanne he started at this time and has almost equally as far of a destination as her meaning he has a lot of ground to cover requiring fast flying speeds. Eric is the slowest as his path begins in the same area as Nico but ends sooner in the same amount of time as the rest so there is no need for him to fly as fast as the other two.  

During these months which bird travelled the farthest distance?

In [19]:
import math
from math import *

def dist(lon1,lat1,lon2,lat2):
    lon1,lat1,lon2,lat2 = map(radians,[lon1,lat1,lon2,lat2])
    dlon = lon2-lon1
    dlat = lat2-lat1
    a = sin(dlat/2)**2 + cos(lat1) * cos(lat2) * sin(dlon/2)**2
    c = 2 * asin(sqrt(a))
    r = 6371
    return c * r
def dist_bird(bird):
    dist_df = migration_df[migration_df['bird_name'] == bird]
    dist_df = dist_df.assign(date = lambda d: pd.to_datetime(d['date_time']))
    dist_df['travelled'] = 0 
    dist_df = dist_df.reset_index()
    for i in range(len(dist_df)-1):
        travelled = dist(dist_df.loc[i,'longitude'],dist_df.loc[i,'latitude'],dist_df.loc[i+1,'longitude'],dist_df.loc[i+1,'latitude'])
        dist_df.loc[i+1,'travelled'] = travelled
    return dist_df['travelled'].sum()

In [24]:
print('Erics distance travelled from November to February:',round(dist_bird('Eric'),2))
print('Sannes distance travelled from November to February:',round(dist_bird('Sanne'),2))
print('Nicos distance travelled from November to February:',round(dist_bird('Nico'),2))

Erics distance travlled from November to February: 8500.34
Sannes distance travlled from November to February: 11015.96
Nicos distance travlled from November to February: 12095.48


As we had seen from the previous map and had assumed from the speed distribution for each bird Eric travelled the least amount of space within this timeframe. Sanne like her speed was in the middle which once again makes sense based off of the previously analyzed data as visually it looked like she travelled the second most amount of space and because of her speed being in the middle of the pack. Finally as it was assumed by looking at the map and speed distribution Nico travelled the most out of any bird from November to February as he did not begin his southern flight until this month unlike Sanne who from looking back at the August data began her journey south and was going to a destination at the end of February near where Nico was going to end up which accounts for Nico needing to travel significantly more than his counterparts. 

## Main Takeaways and Overall Review/Conclusions
- While during August Sanne appears to be the most active overall from November to February it is Nico who travels the most and flies the fastest on average making him the most active of that timeframe
- No matter the time in August it appears the birds stay quite conistent in their paths/activity
- Sanne appears to begin making her southern migration in August, significantly earlier than Nico or Eric who do not appear to start until November, hence her altitude being much lower on average being so close to sea level across the coastline
- From the data we looked at Eric is not only the slowest bird, but travels the shortest distance as well
- Nico is the most active due to the fact it appears he along with Eric do not begin their travel southward until this time period way after Sanne, and he has more distnace to cover to get to his final destination during this period compared to Eric whos path in this data stops in Morroco. Nico goes all the way to Mauritania. 
- Based on their starting and end points and outisde research from rspb.org it is possible that these birds are Swallows as they usually begin in France like the one's from our data and end either in Morroco like Eric or more Southern Africa like Sanne and Nico